In [27]:
import json
import pymongo
import multiprocessing as mp

client = pymongo.MongoClient("mongodb://localhost:27017/")

with open("dep_resolve/top-pypi-packages-30-days.min.json") as f:
    packages = [r["project"].lower() for r in json.load(f)["rows"]]

def worker(pkg_name):
    results = []
    all_dists = list(client["pypi"]["distribution_metadata"].find({"name": pkg_name}))
    vers = set(dist["version"] for dist in all_dists)
    for ver in vers:
        dists = [d for d in all_dists if d["version"] == ver]
        dists = [str(sorted(dist["requires_dist"])) for dist in dists if len(dist["requires_dist"]) > 0]
        dists = ["".join(d.split()) for d in dists]
        if len(set(dists)) > 1:
            results.append((pkg_name, ver))
    return results

with mp.Pool(mp.cpu_count()) as pool:
    bad_pairs = set(sum(pool.map(worker, packages), []))
print(len(bad_pairs))

541


In [34]:
all_dists = list(client["pypi"]["distribution_metadata"].find({"name": {"$in": packages}}))
print(len(all_dists), "distributions")
print(len(set((d["name"], d["version"]) for d in all_dists)), "versions")
print(len(set(d["name"] for d in all_dists)), "packages")

676018 distributions
193674 versions
4399 packages


In [28]:
for pkg, ver in bad_pairs:
    print(pkg, ver)
    dists = list(client["pypi"]["distribution_metadata"].find({"name": pkg, "version": ver}))
    dists = [str(sorted(dist["requires_dist"])) for dist in dists if len(dist["requires_dist"]) > 0]
    for dist in dists:
        print("  ", dist)

tcod 11.19.1
   ['cffi (~=1.13)', 'typing-extensions']
   ['cffi (~=1.13)', 'numpy (~=1.10)', 'typing-extensions']
   ['cffi (~=1.13)', 'typing-extensions']
blspy 0.2.4
   ['pybind11 (>=2.5.0)']
   ['pybind11 (>=2.5.0)']
   ['wheel']
   ['wheel']
   ['pybind11 (>=2.5.0)']
pillow-heif 0.7.2
   ['cffi (>=1.14.6)', "coverage ; extra == 'dev'", "defusedxml ; extra == 'dev'", "defusedxml ; extra == 'tests'", "defusedxml ; extra == 'tests-min'", "numpy ; extra == 'dev'", "numpy ; extra == 'tests'", "opencv-python ; extra == 'dev'", "packaging ; extra == 'dev'", "packaging ; extra == 'tests'", "packaging ; extra == 'tests-min'", "piexif ; extra == 'dev'", "piexif ; extra == 'tests'", "piexif ; extra == 'tests-min'", 'pillow (>=6.2.0)', "pre-commit ; extra == 'dev'", "pylint (<=2.14.5) ; extra == 'dev'", "pympler ; extra == 'dev'", "pympler ; extra == 'tests'", "pytest ; extra == 'dev'", "pytest ; extra == 'tests'", "pytest ; extra == 'tests-min'", "sphinx (>=4.4) ; extra == 'docs'", "sphinx-i